# Try DMC Tracking Env directly

In [1]:
import numpy as np
import PIL.ImageDraw

import tensorflow as tf
import tensorflow_probability as tfp
from acme import wrappers

from flybody.basic_rodent_2020 import (
    walk_imitation,
    walk_humanoid,
    rodent_escape_bowl,
    rodent_run_gaps
)

from flybody.agents.utils_tf import TestPolicyWrapper
from flybody.utils import (
    display_video,
    rollout_and_render,
)

from flybody.fruitfly import rodent

from dm_control import composer
from dm_control.locomotion import arenas
from dm_control.locomotion import walkers
from dm_control.locomotion.walkers import rodent
from dm_control.locomotion.mocap import props
from dm_control.locomotion.tasks.reference_pose import tracking
from dm_control.locomotion.tasks.reference_pose import types
from dm_control.utils import io as resources
import os
import h5py

In [3]:
REF_WALK_RODENT = "/root/talmolab-smb/kaiwen/flybody/clips/all_snippets.h5"
OUT = "/root/talmolab-smb/kaiwen/flybody/clips/only_walk.h5"

In [13]:
import h5py
from flybody.tasks.trajectory_rodent import read_h5_file

def copy_walk_clips(original_file_path, new_file_path):
    with h5py.File(original_file_path, 'r') as original_file, h5py.File(new_file_path, 'w') as new_file:
        for clip_name in original_file.keys():
            clip_group = original_file[clip_name]
            action = clip_group.attrs.get('action', '')
            # if 'Walk' in action:
            if clip_name == "clip_614":
                new_file.copy(clip_group, clip_name)
                new_file[clip_name].attrs['action'] = action
                new_file[clip_name].attrs['dt'] = clip_group.attrs.get('dt', 0.02)
                new_file[clip_name].attrs['num_steps'] = clip_group.attrs.get('num_steps', 250)

copy_walk_clips(REF_WALK_RODENT, OUT)

In [ ]:
read_h5_file(OUT)

In [1]:
# Define the path to your motion capture data file
file_name = REF_WALK_RODENT
current_directory = os.getcwd()
TEST_FILE_PATH = os.path.join(current_directory, file_name)

with h5py.File(TEST_FILE_PATH, 'r') as f:
    dataset_keys = tuple(f.keys())
    dataset = types.ClipCollection(ids=dataset_keys,)

# Set up the mocap tracking task
task = tracking.MultiClipMocapTracking(
    walker=rodent.Rat,
    arena=arenas.Floor(),
    ref_path=resources.GetResourceFilename(TEST_FILE_PATH),
    ref_steps=(1, 2, 3, 4, 5),
    min_steps=1,
    dataset=dataset,
    reward_type='comic',
    always_init_at_clip_start=True
)

# Initialize the environment
env = composer.Environment(task=task)
reset = env.reset()

NameError: name 'REF_WALK_RODENT' is not defined

# Instantiate Environment

In [12]:
ref_traj_path = "/root/talmolab-smb/kaiwen/flybody/clips/all_snippets.h5"
env = walk_imitation(ref_traj_path)

In [4]:
env.observation_spec()

OrderedDict([('reference_props_pos_global',
              Array(shape=(0,), dtype=dtype('float64'), name='reference_props_pos_global')),
             ('reference_props_quat_global',
              Array(shape=(0,), dtype=dtype('float64'), name='reference_props_quat_global')),
             ('walker/actuator_activation',
              Array(shape=(38,), dtype=dtype('float64'), name='walker/actuator_activation')),
             ('walker/appendages_pos',
              Array(shape=(15,), dtype=dtype('float64'), name='walker/appendages_pos')),
             ('walker/body_height',
              Array(shape=(), dtype=dtype('float64'), name='walker/body_height')),
             ('walker/end_effectors_pos',
              Array(shape=(12,), dtype=dtype('float64'), name='walker/end_effectors_pos')),
             ('walker/joints_pos',
              Array(shape=(30,), dtype=dtype('float64'), name='walker/joints_pos')),
             ('walker/joints_vel',
              Array(shape=(30,), dtype=dtype('floa

In [5]:
env.action_spec()

BoundedArray(shape=(38,), dtype=dtype('float64'), name='walker/lumbar_extend\twalker/lumbar_bend\twalker/lumbar_twist\twalker/cervical_extend\twalker/cervical_bend\twalker/cervical_twist\twalker/caudal_extend\twalker/caudal_bend\twalker/hip_L_supinate\twalker/hip_L_abduct\twalker/hip_L_extend\twalker/knee_L\twalker/ankle_L\twalker/toe_L\twalker/hip_R_supinate\twalker/hip_R_abduct\twalker/hip_R_extend\twalker/knee_R\twalker/ankle_R\twalker/toe_R\twalker/atlas\twalker/mandible\twalker/scapula_L_supinate\twalker/scapula_L_abduct\twalker/scapula_L_extend\twalker/shoulder_L\twalker/shoulder_sup_L\twalker/elbow_L\twalker/wrist_L\twalker/finger_L\twalker/scapula_R_supinate\twalker/scapula_R_abduct\twalker/scapula_R_extend\twalker/shoulder_R\twalker/shoulder_sup_R\twalker/elbow_R\twalker/wrist_R\twalker/finger_R', minimum=[-1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1.
 -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1. -1.
 -1. -1.], maximum=[1. 1. 1.

In [6]:
timestep = env.reset()

In [7]:
timestep.observation.keys()

odict_keys(['reference_props_pos_global', 'reference_props_quat_global', 'walker/actuator_activation', 'walker/appendages_pos', 'walker/body_height', 'walker/end_effectors_pos', 'walker/joints_pos', 'walker/joints_vel', 'walker/sensors_accelerometer', 'walker/sensors_force', 'walker/sensors_gyro', 'walker/sensors_torque', 'walker/sensors_touch', 'walker/sensors_velocimeter', 'walker/tendons_pos', 'walker/tendons_vel', 'walker/world_zaxis', 'walker/reference_rel_joints', 'walker/reference_rel_bodies_pos_global', 'walker/reference_rel_bodies_quats', 'walker/reference_rel_bodies_pos_local', 'walker/reference_ego_bodies_quats', 'walker/reference_rel_root_quat', 'walker/reference_rel_root_pos_local', 'walker/reference_appendages_pos', 'walker/clip_id', 'walker/velocimeter_control', 'walker/gyro_control', 'walker/joints_vel_control', 'walker/time_in_clip'])

In [8]:
env2 = rodent_run_gaps()
timestep = env2.reset()

In [9]:
timestep.observation

OrderedDict([('walker/actuator_activation',
              array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
                     0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
                     0., 0., 0., 0.])),
             ('walker/appendages_pos',
              array([ 1.93287916e-02, -2.18352854e-02, -3.62436917e-02,  1.93287916e-02,
                      2.18352854e-02, -3.62436917e-02, -8.59399785e-02, -2.42398919e-02,
                     -5.59274288e-02, -8.59399785e-02,  2.42465031e-02, -5.59274288e-02,
                      6.62354248e-02, -1.83587305e-07,  7.40654969e-03])),
             ('walker/body_height', array(0.06508957)),
             ('walker/egocentric_camera',
              array([[[ 33, 125, 195],
                      [ 32, 124, 195],
                      [ 32, 124, 195],
                      ...,
                      [137, 161, 186],
                      [158, 169, 181],
                      [164, 171, 178]

In [10]:
n_actions = env.action_spec().shape[0]

def random_action_policy(observation):
    del observation  # Not used by dummy policy.
    random_action = np.random.uniform(-.5, .5, n_actions)
    return random_action

frames = []
rewards = []

timestep = env.reset()
for _ in range(250):
    
    action = random_action_policy(timestep.observation)
    timestep = env.step(action)
    rewards.append(timestep.reward)

    pixels = env.physics.render(camera_id=1)
    frames.append(pixels)

display_video(frames)

In [ ]:
frames = []
rewards = []

timestep = env.reset()
for _ in range(100):
    
    action = random_action_policy(timestep.observation)
    timestep = env.step(action)
    rewards.append(timestep.reward)

    pixels = env.physics.render(camera_id=1)
    frames.append(pixels)

display_video(frames)

In [ ]:
frames = []
rewards = []

timestep = env.reset()
for _ in range(150):
    
    action = random_action_policy(timestep.observation)
    timestep = env.step(action)
    rewards.append(timestep.reward)

    pixels = env.physics.render(camera_id=1)
    frames.append(pixels)

display_video(frames)

In [ ]:
frames = []
rewards = []

timestep = env.reset()
for _ in range(150):
    
    action = random_action_policy(timestep.observation)
    timestep = env.step(action)
    rewards.append(timestep.reward)

    pixels = env.physics.render(camera_id=1)
    frames.append(pixels)

display_video(frames)

# Humanoid

In [15]:
ref_traj_path = "/root/talmolab-smb/kaiwen/flybody/clips/cmu_2020_dfe3e9e0.h5"
read_h5_file(ref_traj_path)

Group: CMU_001_01
CMU_001_01:
    day: 0
    dt: 0.03
    month: 0
    num_steps: 761
    year: 0
Group: CMU_001_01/props
CMU_001_01/props:
Group: CMU_001_01/walkers
CMU_001_01/walkers:
Group: CMU_001_01/walkers/walker_0
CMU_001_01/walkers/walker_0:
    appendage_names: [b'rradius' b'lradius' b'rfoot' b'lfoot' b'head']
    end_effector_names: [b'rradius' b'lradius' b'rfoot' b'lfoot']
    mass: 70.0
    model: 4
    name: CMU_2020
Dataset: CMU_001_01/walkers/walker_0/angular_velocity
    shape: (3, 761)
    dtype: float32
Dataset: CMU_001_01/walkers/walker_0/appendages
    shape: (15, 761)
    dtype: float32
Dataset: CMU_001_01/walkers/walker_0/body_positions
    shape: (93, 761)
    dtype: float32
Dataset: CMU_001_01/walkers/walker_0/body_quaternions
    shape: (124, 761)
    dtype: float32
Dataset: CMU_001_01/walkers/walker_0/center_of_mass
    shape: (3, 761)
    dtype: float32
Dataset: CMU_001_01/walkers/walker_0/end_effectors
    shape: (12, 761)
    dtype: float32
Dataset: CMU_001

In [18]:
ref_traj_path = "/root/talmolab-smb/kaiwen/flybody/clips/test_trajectories.h5"
read_h5_file(ref_traj_path)

Group: cmuv2019_001
cmuv2019_001:
    day: 7
    dt: 0.05
    month: 7
    num_steps: 10
    year: 2020
Group: cmuv2019_001/props
cmuv2019_001/props:
Group: cmuv2019_001/props/prop_0
cmuv2019_001/props/prop_0:
    mass: 3.0
    name: b'cmuv2019_box'
    shape: 2
    size: [0.1775 0.1275 0.1775]
Dataset: cmuv2019_001/props/prop_0/angular_velocity
    shape: (3, 10)
    dtype: float64
Dataset: cmuv2019_001/props/prop_0/position
    shape: (3, 10)
    dtype: float64
Dataset: cmuv2019_001/props/prop_0/quaternion
    shape: (4, 10)
    dtype: float64
Dataset: cmuv2019_001/props/prop_0/velocity
    shape: (3, 10)
    dtype: float64
Group: cmuv2019_001/walkers
cmuv2019_001/walkers:
Group: cmuv2019_001/walkers/walker_0
cmuv2019_001/walkers/walker_0:
    appendage_names: []
    end_effector_names: []
    mass: 0.0
    model: 1
    name: b'cmuv2019_CMU'
Dataset: cmuv2019_001/walkers/walker_0/angular_velocity
    shape: (3, 10)
    dtype: float64
Dataset: cmuv2019_001/walkers/walker_0/appendages


In [3]:
from dm_control.locomotion.mocap import cmu_mocap_data

In [24]:
cmu_mocap_data.get_path_for_cmu(version='2019')

'/root/anaconda3/envs/flybody/lib/python3.10/site-packages/dm_control/locomotion/mocap/cmu_2019_08756c01.h5'

In [4]:
env = walk_humanoid('cmu_2020_dfe3e9e0.h5')

In [5]:
env.observation_spec()

OrderedDict([('reference_props_pos_global',
              Array(shape=(0,), dtype=dtype('float64'), name='reference_props_pos_global')),
             ('reference_props_quat_global',
              Array(shape=(0,), dtype=dtype('float64'), name='reference_props_quat_global')),
             ('walker/actuator_activation',
              Array(shape=(56,), dtype=dtype('float64'), name='walker/actuator_activation')),
             ('walker/appendages_pos',
              Array(shape=(15,), dtype=dtype('float64'), name='walker/appendages_pos')),
             ('walker/body_height',
              Array(shape=(), dtype=dtype('float64'), name='walker/body_height')),
             ('walker/end_effectors_pos',
              Array(shape=(12,), dtype=dtype('float64'), name='walker/end_effectors_pos')),
             ('walker/joints_pos',
              Array(shape=(56,), dtype=dtype('float64'), name='walker/joints_pos')),
             ('walker/joints_vel',
              Array(shape=(56,), dtype=dtype('floa

In [8]:
# Frame width and height for rendering.
render_kwargs = {'width': 640, 'height': 480}

n_actions = env.action_spec().shape[0]

def random_action_policy(observation):
    del observation  # Not used by dummy policy.
    random_action = np.random.uniform(-.5, .5, n_actions)
    return random_action

frames = []
rewards = []

timestep = env.reset()
for _ in range(500):
    
    action = random_action_policy(timestep.observation)
    timestep = env.step(action)
    rewards.append(timestep.reward)

    pixels = env.physics.render(camera_id=1, **render_kwargs)
    frames.append(pixels)

display_video(frames)

In [9]:
import os

from dm_control.mjcf import constants
from dm_control.mujoco.wrapper import util


def export_with_assets(mjcf_model, out_dir, out_file_name=None,
                       *,
                       precision=constants.XML_DEFAULT_PRECISION,
                       zero_threshold=0):
  """Saves mjcf.model in the given directory in MJCF (XML) format.

  Creates an MJCF XML file named `out_file_name` in the specified `out_dir`, and
  writes all of its assets into the same directory.

  Args:
    mjcf_model: `mjcf.RootElement` instance to export.
    out_dir: Directory to save the model and assets. Will be created if it does
      not already exist.
    out_file_name: (Optional) Name of the XML file to create. Defaults to the
      model name (`mjcf_model.model`) suffixed with '.xml'.
    precision: (optional) Number of digits to output for floating point
      quantities.
    zero_threshold: (optional) When outputting XML, floating point quantities
      whose absolute value falls below this threshold will be treated as zero.

  Raises:
    ValueError: If `out_file_name` is a string that does not end with '.xml'.
  """
  if out_file_name is None:
    out_file_name = mjcf_model.model + '.xml'
  elif not out_file_name.lower().endswith('.xml'):
    raise ValueError('If `out_file_name` is specified it must end with '
                     '\'.xml\': got {}'.format(out_file_name))
  assets = mjcf_model.get_assets()
  # This should never happen because `mjcf` does not support `.xml` assets.
  assert out_file_name not in assets
  assets[out_file_name] = mjcf_model.to_xml_string(
      precision=precision, zero_threshold=zero_threshold)
  if not os.path.exists(out_dir):
    os.makedirs(out_dir)
  for filename, contents in assets.items():
    with open(os.path.join(out_dir, filename), 'wb') as f:
      f.write(util.to_binary_string(contents))

In [15]:
env.physics

AttributeError: 'Physics' object has no attribute 'mj_model'

In [8]:
export_with_assets(env.physics, "/root/talmolab-smb/kaiwen/flybody/docs/", "rodent_env_xml.xml")

AttributeError: 'Physics' object has no attribute 'get_assets'